In [1]:
import pandas as pd
import numpy as np
import seaborn as sns

from nltk.tokenize import word_tokenize, PunktSentenceTokenizer, TreebankWordTokenizer
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.wordnet import WordNetLemmatizer

from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import linear_kernel
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer


/anaconda3/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/anaconda3/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/anaconda3/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


In [2]:
public_df = pd.read_csv('data/public-study/EmoTrak-emotrak-2018-04-19T20_50_09.379Z.csv')

In [3]:
pd.set_option('display.max_columns', 999)

In [4]:
train, test = train_test_split(public_df, shuffle=True)

In [6]:
train.shape

(5569, 59)

In [7]:
train['specificEmotion'] = train['specificEmotion'].replace('embarrased', 'embarrassed')

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [10]:
train['trigger'].apply(type).unique()

array([<class 'str'>, <class 'float'>], dtype=object)

In [13]:
new_train = train.drop(train[train['trigger'].apply(type) == float].index)

In [15]:
new_train['trigger'].apply(type).unique()

array([<class 'str'>], dtype=object)

In [16]:
stop = set(stopwords.words('english'))

In [18]:
treebank_word_tokenize = TreebankWordTokenizer().tokenize
tokens = [treebank_word_tokenize(content.lower()) for content in new_train['trigger']]

In [20]:
docs = [[word for word in words if word not in stop]
        for words in tokens]

In [21]:
porter = PorterStemmer()
snowball = SnowballStemmer('english')
wordnet = WordNetLemmatizer()

docs_porter = [[porter.stem(word) for word in words]
               for words in docs]
docs_snowball = [[snowball.stem(word) for word in words]
                 for words in docs]
docs_wordnet = [[wordnet.lemmatize(word) for word in words]
                for words in docs]

In [26]:
print("%16s %16s %16s %16s" % ("word", "porter", "snowball", "lemmatizer"))
for i in range(min(len(docs_porter[5]), len(docs_snowball[5]), len(docs_wordnet[5]))):
    p, s, w = docs_porter[5][i], docs_snowball[5][i], docs_wordnet[5][i]
    if len(set((p, s, w))) != 1:
        print("%16s %16s %16s %16s" % (docs[5][i], p, s, w))

            word           porter         snowball       lemmatizer
           going               go               go            going
        vacation            vacat            vacat         vacation
        visiting            visit            visit         visiting
            baby             babi             babi             baby
         excited            excit            excit          excited
      frustrated         frustrat         frustrat       frustrated


In [36]:
docs

[['walking', 'rose', 'japanese', 'gardens', 'ed', '.'],
 ['election'],
 ['interaction', 'earlier', 'day'],
 ['thinking',
  'work.',
  'worried',
  'upcoming',
  'week.',
  'thought',
  'teach',
  'felt',
  'somewhat',
  'better',
  '.'],
 ['unable', 'settle', 'work.', 'distracted.', 'need', 'fresh', 'air'],
 ['wife',
  'going',
  'town',
  'vacation',
  'parents',
  'also',
  'visiting',
  ',',
  'baby',
  'got',
  'excited',
  'frustrated',
  'would',
  "n't",
  'sleep',
  '.'],
 ['moved', 'mode', 'long', 'term', 'financial', 'picture', '&', 'capability'],
 ['thinking', 'work'],
 ['coworker',
  'struggling',
  'issues',
  'really',
  'pleasant',
  'around',
  'moment.',
  'looking',
  'forward',
  'long',
  'day',
  'ahead',
  'trying',
  'patient'],
 ['busy', 'day'],
 ['spiritual', 'practice', 'friends'],
 ['deadline',
  "'m",
  'going',
  'miss',
  'concerned',
  'ramifications.',
  'time',
  'feeling',
  'guilty',
  'present',
  'family',
  '.'],
 ['home'],
 ['tapping',
  'feet',
 

In [27]:
def tokenize(doc):
    '''
    INPUT: string
    OUTPUT: list of strings

    Tokenize and stem/lemmatize the document.
    '''
    return [wordnet.lemmatize(word) for word in word_tokenize(doc.lower())]

In [28]:
countvect = CountVectorizer(stop_words='english', tokenizer=tokenize)
count_vectorized = countvect.fit_transform(new_train['trigger'])

In [29]:
words = countvect.get_feature_names()

In [35]:
words

['!',
 '#',
 '$',
 '%',
 '&',
 "'",
 "''",
 "'d",
 "'get",
 "'ll",
 "'m",
 "'missing",
 "'re",
 "'s",
 "'ve",
 '(',
 ')',
 '+',
 '+absence',
 ',',
 '-',
 '--',
 '-chill',
 '-error',
 '.',
 '..',
 '...',
 '.off',
 '.possibly',
 '/',
 '/side',
 '/stretching',
 '1',
 '1.',
 '1/2',
 '10',
 '11',
 '12',
 '13',
 '130',
 '15',
 '18',
 '1968',
 '1:1',
 '1hr',
 '1st',
 '2',
 '2-mile',
 '2.',
 '20',
 '24',
 '24hr',
 '25',
 '25th',
 '28',
 '2:30',
 '2hours',
 '2nd',
 '3',
 '3-4times',
 '3-day',
 '3-months',
 '3.30pm',
 '30',
 '30-something',
 '30mins',
 '32',
 '36',
 '37',
 '3am',
 '3hours',
 '4',
 '4-5',
 '4.5',
 '40',
 '400',
 '45',
 '49',
 '4yo',
 '5',
 '5-7',
 '5.3.',
 '50',
 '545',
 '55',
 '5:00',
 '5:30',
 '5:30h',
 '5:50',
 '5k',
 '6',
 '60',
 '630',
 '6:15h',
 '7',
 '7.4km',
 '71.',
 '80',
 '82',
 '87',
 '8pm',
 '9',
 '90',
 ':',
 ';',
 '=',
 '?',
 '[',
 ']',
 '``',
 'a.',
 'a/c',
 'aaaaargh',
 'aap',
 'abandoned',
 'abdomen',
 'ability',
 'able',
 'abound',
 'abraham',
 'abrasive',
 'abr

In [32]:
tfidfvect = TfidfVectorizer(stop_words='english', tokenizer=tokenize)
tfidf_vectorized = tfidfvect.fit_transform(new_train['trigger'])

In [33]:
cosine_similarities = linear_kernel(tfidf_vectorized, tfidf_vectorized)

In [34]:
for i, doc1 in enumerate(docs):
    for j, doc2 in enumerate(docs):
        print(i, j, cosine_similarities[i, j])

0 0 1.0
0 1 0.0
0 2 0.0
0 3 0.04779880791273612
0 4 0.03347384344314675
0 5 0.015471878504141877
0 6 0.0
0 7 0.0
0 8 0.014976232907256238
0 9 0.0
0 10 0.0
0 11 0.030907099473130455
0 12 0.0
0 13 0.017168137091934394
0 14 0.0
0 15 0.01907973025441678
0 16 0.012329074046337513
0 17 0.0
0 18 0.0
0 19 0.0
0 20 0.0
0 21 0.0
0 22 0.0
0 23 0.0
0 24 0.0
0 25 0.0
0 26 0.0
0 27 0.0
0 28 0.0
0 29 0.010067391850562815
0 30 0.028560134033298268
0 31 0.0
0 32 0.027027026961643177
0 33 0.0
0 34 0.0
0 35 0.0
0 36 0.0
0 37 0.0
0 38 0.0
0 39 0.022527336588742546
0 40 0.020920626198289046
0 41 0.0
0 42 0.0
0 43 0.01455132298905194
0 44 0.0
0 45 0.0
0 46 0.0
0 47 0.0
0 48 0.012912207199397818
0 49 0.0
0 50 0.020839064365974543
0 51 0.0
0 52 0.0
0 53 0.0
0 54 0.0
0 55 0.0
0 56 0.0
0 57 0.0
0 58 0.04454824260878026
0 59 0.0
0 60 0.02237504463316449
0 61 0.0
0 62 0.0
0 63 0.0
0 64 0.0
0 65 0.0
0 66 0.020683219613022594
0 67 0.019095972886043627
0 68 0.013717599446477241
0 69 0.028180136359543053
0 70 0.01277

ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py", line 2910, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-34-ea53c82939fd>", line 3, in <module>
    print(i, j, cosine_similarities[i, j])
  File "/anaconda3/lib/python3.6/site-packages/ipykernel/iostream.py", line 376, in write
    self.pub_thread.schedule(lambda : self._buffer.write(string))
  File "/anaconda3/lib/python3.6/site-packages/ipykernel/iostream.py", line 203, in schedule
    self._event_pipe.send(b'')
  File "zmq/backend/cython/socket.pyx", line 636, in zmq.backend.cython.socket.Socket.send
  File "zmq/backend/cython/socket.pyx", line 683, in zmq.backend.cython.socket.Socket.send
  File "zmq/backend/cython/socket.pyx", line 201, in zmq.backend.cython.socket._send_copy
  File "zmq/backend/cython/checkrc.pxd", line 12, in zmq.backend.cython.checkrc._check_rc
KeyboardInterrupt

During handling of the above exception, 

KeyboardInterrupt: 